In [ ]:
!pip install icrawler -q
!pip install -U ddgs -q


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 41.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 75.3 MB/s eta 0:00:00


In [ ]:
import os
import time
import requests
import shutil
from icrawler.builtin import  (BingImageCrawler,GoogleImageCrawler)
from ddgs import DDGS
import hashlib

In [ ]:
def DDG_search_images(term, min_images=300):
  """
  term: term we are searching for
  min_images: minimum number of images to be downloaded
  """
  results = []
  for page_no in range(1, 50): # continue to traverse pages until we get the target no of images
    responses = DDGS().images(
        query=term,
        region="us-en",
        safesearch="off",
        timelimit="y",
        max_results=min_images,
        page = page_no,
        backend="auto",
    )
    results.extend(responses)
    if len(results) >= min_images: break

  image_urls = [result['image'] for result in results]
  return image_urls

In [ ]:
#image duplicate remover

def file_hash(path):
    with open(path, 'rb') as f:
        return hashlib.md5(f.read()).hexdigest()

def deduplicate(src_dir):
    """Remove duplicate files in-place (keeps only first occurrence)."""
    hashes = {}
    removed = 0

    for fname in os.listdir(src_dir):
        fpath = os.path.join(src_dir, fname)
        if not os.path.isfile(fpath):
            continue

        h = file_hash(fpath)
        if h in hashes:
            os.remove(fpath)  # delete duplicate
            removed += 1
        else:
            hashes[h] = fpath

    print(f"[{src_dir}] Removed {removed} duplicates")

In [ ]:

def download_images(class_name, keywords):

  """ Scrape image from 3 source for each class based on keywords --> combine them --> keep only jpg format --> removes duplicate. """

    search_filters_bing = dict()


    for kw in keywords:

      folder_name = kw.replace(" ", "_")
      google_crawler = GoogleImageCrawler(downloader_threads=4,storage={'root_dir': f'{class_name}_google/{folder_name}'})
      bing_crawler = BingImageCrawler(downloader_threads=4,storage={'root_dir': f'{class_name}_bing/{folder_name}'})

      bing_crawler.crawl(keyword=kw, filters=search_filters_bing, max_num=1000)
      google_crawler.crawl(keyword=kw, filters=search_filters_bing, max_num=1000)

      images = DDG_search_images(kw)

      download_folder = f'{class_name}_duck/{folder_name}'
      os.makedirs(download_folder, exist_ok=True)

      count = 1

      for link in images:
          try:
              # get extension and clean it
              ext = os.path.splitext(link)[1].lower()

              # build filename (6-digit padded)
              filename = f"{str(count).zfill(6)}{ext}"
              filepath = os.path.join(download_folder, filename)

              # download image
              response = requests.get(link, stream=True, timeout=10)
              response.raise_for_status()

              with open(filepath, "wb") as f:
                  for chunk in response.iter_content(chunk_size=8192):
                      f.write(chunk)

              count += 1

          except Exception as e:
              print(f"❌ Skipped {link} — {e}")

      print(f"✅ Downloads complete for '{kw}' — saved {count-1} images.")

    dst_dir = f"/content/{class_name}"
    os.makedirs(dst_dir, exist_ok=True)
    scrpaing_src = ['bing', 'google', 'duck']

    # source and destination folders
    for src in scrpaing_src:
      src_dir = f"/content/{class_name}_{src}"


      for root, _, files in os.walk(src_dir):
          for file in files:
              if file.lower().endswith(('.jpg', '.jpeg')):  # only jpg images
                  src_path = os.path.join(root, file)

                  rel_path = os.path.relpath(src_path, "/content")
                  new_name = rel_path.replace("/", "_")

                  dst_path = os.path.join(dst_dir, new_name)
                  shutil.copy2(src_path, dst_path)


      shutil.rmtree(src_dir)

      print("✅ All images copied and renamed into:", dst_dir)

    deduplicate(dst_dir)


In [ ]:
construction_items = {
    "helmet": ["construction helmet", "construction hat", "hard hat", "safety helmet"],
    "c_vest": ["safety vest", "construction vest", "orange construction vest", "blue construction vest"],
    "boots": ["construction safety boots", "men construction boots", "women construction boots", "work safety boots"],
    "gloves": ["construction gloves", "rubber gloves", "safety gloves", "construction safety gloves"],
    "goggles": ["safety goggles", "construction goggles", "work goggles", "protective goggles"],
    "exvtr": ["excavator", "construction excavator", "heavy duty excavator", "cat excavator"],
    "crn": ["construction crane", "construction truck crane", "telescopic crane", "boom truck"],
    "truck": ["dump truck", "heavy construction truck", "concrete trucks", "construction transport trucks"],
    "worker": ["construction worker", "construction building worker", "heavy worker", "worker in construction"],
    "s_cone": ["safety cone", "construction cone", "work safety cone", "heavy construction cone"],
    "ldr": ["ladder", "construction ladder", "building construction ladder", "heavy construction ladder"],
    "msk": ["construction mask", "full face construction mask", "balaclava construction mask", "construction dust mask"],
}


In [ ]:
for class_name, keywords in construction_items.items():
    download_images(class_name, keywords)


ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2014/05/25__06_24_41/helmet_01.jpg
ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2015/12/14__03_54_34/construction_helmet_3.jpg
ERROR:downloader:Response status code 404, file https://static.stihl.com/upload/assetmanager/modell_imagefilename/scaled/zoom/736bf6f6a3ed4ea0b337f3f2fa4af167.jpg
ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2015/12/14__03_54_34/construction_helmet_5.jpg
ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2014/05/25__06_24_41/helmet_02.jpg
ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2015/12/14__03_54_34/construction_helmet_4.jpg
ERROR:downloader:Response status code 403, file https://static.turbosquid.com/Preview/2015/12/14__03_54_34/construction_helmet_1.jpg
ERROR:downloader:Response status code 403, file https://static.

❌ Skipped https://www.workplacepub.com/wp-content/uploads/2024/01/Milwaukee-Tool-Safety-Helmet.jpg — 403 Client Error: Forbidden for url: https://www.workplacepub.com/wp-content/uploads/2024/01/Milwaukee-Tool-Safety-Helmet.jpg
❌ Skipped https://structuralbd.com/wp-content/uploads/2023/06/best-construction-safety-helmet.jpg — 406 Client Error: Not Acceptable for url: https://structuralbd.com/wp-content/uploads/2023/06/best-construction-safety-helmet.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/024/319/322/original/bold-yellow-construction-safety-helmet-clipart-illustration-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/024/319/322/original/bold-yellow-construction-safety-helmet-clipart-illustration-vector.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/018/967/474/original/construction-helmet-one-line-drawing-style-hard-hat-worker-safety-tools-concept-hand-drawn-illustration-vector.jpg — 

ERROR:downloader:Response status code 403, file http://clipart-library.com/img/1982540.jpg
ERROR:downloader:Exception caught when downloading file https://smashmockup.com/wp-content/uploads/2020/07/hardhat.jpg, error: HTTPSConnectionPool(host='smashmockup.com', port=443): Max retries exceeded with url: /wp-content/uploads/2020/07/hardhat.jpg (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x78ac60f61eb0>: Failed to resolve 'smashmockup.com' ([Errno -2] Name or service not known)")), remaining retry times: 2
ERROR:downloader:Exception caught when downloading file https://www.bigw.com.au/medias/sys_master/images/images/h14/h04/27194638925854.jpg, error: HTTPSConnectionPool(host='www.bigw.com.au', port=443): Read timed out. (read timeout=5), remaining retry times: 2
ERROR:downloader:Response status code 403, file https://clipart-library.com/img/1982378.jpg
ERROR:downloader:Response status code 400, file https://partyshop.co.nz/wp-content/uploads/2009/06/produ

❌ Skipped https://png.pngtree.com/thumb_back/fh260/background/20241124/pngtree-a-group-of-construction-hats-in-orange-and-white-ensuring-safety-image_16635484.jpg — 403 Client Error: Forbidden for url: https://png.pngtree.com/thumb_back/fh260/background/20241124/pngtree-a-group-of-construction-hats-in-orange-and-white-ensuring-safety-image_16635484.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/006/363/772/non_2x/construction-yellow-hard-hat-cartoon-illustration-isolated-object-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/006/363/772/non_2x/construction-yellow-hard-hat-cartoon-illustration-isolated-object-vector.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/018/967/474/original/construction-helmet-one-line-drawing-style-hard-hat-worker-safety-tools-concept-hand-drawn-illustration-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/018

ERROR:downloader:Response status code 403, file https://protekta.co.za/wp-content/uploads/2018/11/SA-HARDHAT-OR_Hard-Hat-Orange.jpg
ERROR:downloader:Response status code 403, file https://protekta.co.za/wp-content/uploads/2018/11/SA-HARDHAT-BLUE_Hard-Hat-Standard-Blue.jpg
ERROR:downloader:Response status code 403, file https://protekta.co.za/wp-content/uploads/2018/11/SA-HARDHATN-WH_Nikki-Hard-Hat-White.jpg
ERROR:downloader:Exception caught when downloading file https://mobileindustrialsafetysupplies.com/wp-content/uploads/2015/07/HP24110_B.jpg, error: HTTPSConnectionPool(host='mobileindustrialsafetysupplies.com', port=443): Max retries exceeded with url: /wp-content/uploads/2015/07/HP24110_B.jpg (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: certificate has expired (_ssl.c:1010)'))), remaining retry times: 2
ERROR:downloader:Exception caught when downloading file https://mobileindustrialsafetysupplies.com/wp-content/uploads

...

❌ Skipped https://www.ace-cabletray.com/uploads/202236593/stainless-steel-ladder-cable-tray40330488497.jpg — 403 Client Error: Forbidden for url: https://www.ace-cabletray.com/uploads/202236593/stainless-steel-ladder-cable-tray40330488497.jpg
❌ Skipped https://johnsonfrancis.org/techworld/wp-content/uploads/2025/09/My-DIY-4-to-1-Balun-for-Ladder-Line.jpg — 406 Client Error: Not Acceptable for url: https://johnsonfrancis.org/techworld/wp-content/uploads/2025/09/My-DIY-4-to-1-Balun-for-Ladder-Line.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/011/065/045/original/simple-wooden-straight-ladder-watercolor-style-illustration-isolated-on-white-background-straight-ladder-clipart-cartoon-style-hand-drawn-ladder-ladder-symbol-of-process-and-growth-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/011/065/045/original/simple-wooden-straight-ladder-watercolor-style-illustration-isolated-on-white-background-straight-ladder

ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/157646082/photo/roofer-climbs-ladder-to-get-on-top-of-home.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/180818354/photo/male-construction-worker-climbing-ladder.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/471188535/photo/a-construction-site-worker-climbing-a-ladder.jpg
ERROR:downloader:Response status code 403, file https://c.pxhere.com/photos/07/3b/fall_protection_builder-710585.jpg
ERROR:downloader:Response status code 404, file https://i0.wp.com/civilnoteppt.com/wp-content/uploads/2022/10/19-Types-of-Ladders-All-Guide-on-Ladder.jpg
ERROR:downloader:Response status code 400, file https://media.gettyimages.com/id/522998432/photo/construction-workers-renovating-building.jpg
ERROR:downloader:Response status code 403, file https://static.vecteezy.com/system/resources/previews/013/677/543/non_2x/set-of-three-construction-tools-on

❌ Skipped https://safetycounselling.com/wp-content/uploads/2021/08/Construction-Site-Safety-Using-Extension-Ladders-Safely-by-Safety-Counselling-505-881-1112-scaled.jpg — 403 Client Error: Forbidden for url: https://safetycounselling.com/wp-content/uploads/2021/08/Construction-Site-Safety-Using-Extension-Ladders-Safely-by-Safety-Counselling-505-881-1112-scaled.jpg
❌ Skipped https://www.mrbricolage.com.cy/wp-content/uploads/2025/02/010-049-161-0301.jpg — 403 Client Error: Forbidden for url: https://www.mrbricolage.com.cy/wp-content/uploads/2025/02/010-049-161-0301.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/058/223/636/non_2x/a-glyph-style-icon-of-construction-ladder-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/058/223/636/non_2x/a-glyph-style-icon-of-construction-ladder-vector.jpg
❌ Skipped https://www.theladders.com/static/images/ladders-default-og.jpg — 403 Client Error: Forbidden for url: https://www.

ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/180818354/photo/male-construction-worker-climbing-ladder.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/488947244/photo/construction-ladder-in-wooden-building-restoration.jpg
ERROR:downloader:Response status code 400, file https://media.gettyimages.com/id/522998432/photo/construction-workers-renovating-building.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/1199844198/photo/wooden-ladders-and-unfinished-buildings-in-the-construction-site.jpg
ERROR:downloader:Response status code 403, file https://www.insideadvisorpro.com/wp-content/uploads/2023/09/Young-man-carrying-ladder-on-construction-site.jpg
ERROR:downloader:Response status code 403, file https://static.vecteezy.com/system/resources/previews/013/677/543/non_2x/set-of-three-construction-tools-on-a-ladder-hammer-pliers-and-screwdriver-free-photo.jpg
ERROR:downloader:Response st

DDGSException: No results found.

In [ ]:
construction_items_2 = {"ldr": ["ladder", "construction ladder", "building construction ladder", "heavy construction ladder"],
    "msk": ["construction mask", "full face construction mask", "balaclava construction mask", "construction dust mask"],}

In [ ]:
!rm -rf /content/ldr_google

In [ ]:
for class_name, keywords in construction_items_2.items():
    download_images(class_name, keywords)


ERROR:downloader:Response status code 404, file https://cdn11.bigcommerce.com/s-nu76q5988i/images/stencil/2560w/g/6206_pi__87990.original.jpg
ERROR:downloader:Response status code 404, file https://cdn11.bigcommerce.com/s-nu76q5988i/images/stencil/2560w/a/fmt-17_pi_jpeg1000__33381.original.jpg
ERROR:downloader:Response status code 404, file https://cdn11.bigcommerce.com/s-nu76q5988i/images/stencil/2560w/g/d6220-2_pi_jpeg1000__88231.original.jpg
ERROR:downloader:Response status code 404, file https://www.laddertool.com/img/product/pro/3_1/apc_05_xl.jpg
ERROR:downloader:Exception caught when downloading file http://www.homedepot.com/catalog/productImages/1000/3e/3e803f6d-04dc-4055-868b-9a0894178ba0_1000.jpg, error: HTTPSConnectionPool(host='images.thdstatic.com', port=443): Read timed out. (read timeout=5), remaining retry times: 2
ERROR:downloader:Response status code 404, file https://cdn11.bigcommerce.com/s-nu76q5988i/images/stencil/2560w/t/t6206_pi__65579.original.jpg
ERROR:downloade

❌ Skipped https://static.vecteezy.com/system/resources/previews/011/065/045/original/simple-wooden-straight-ladder-watercolor-style-illustration-isolated-on-white-background-straight-ladder-clipart-cartoon-style-hand-drawn-ladder-ladder-symbol-of-process-and-growth-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/011/065/045/original/simple-wooden-straight-ladder-watercolor-style-illustration-isolated-on-white-background-straight-ladder-clipart-cartoon-style-hand-drawn-ladder-ladder-symbol-of-process-and-growth-vector.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/022/186/246/original/choosing-success-ladder-difference-career-path-opportunity-or-various-choices-challenge-to-choose-best-option-climb-up-ladder-of-success-concept-businessman-thinking-to-choose-the-right-ladder-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/022/186/246/original/choosing-succe

ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/157646082/photo/roofer-climbs-ladder-to-get-on-top-of-home.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/180818354/photo/male-construction-worker-climbing-ladder.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/471188535/photo/a-construction-site-worker-climbing-a-ladder.jpg
ERROR:downloader:Response status code 404, file https://i0.wp.com/civilnoteppt.com/wp-content/uploads/2022/10/19-Types-of-Ladders-All-Guide-on-Ladder.jpg
ERROR:downloader:Response status code 403, file https://c.pxhere.com/photos/07/3b/fall_protection_builder-710585.jpg
ERROR:downloader:Response status code 400, file https://media.gettyimages.com/id/522998432/photo/construction-workers-renovating-building.jpg
ERROR:downloader:Response status code 403, file https://static.vecteezy.com/system/resources/previews/013/677/543/non_2x/set-of-three-construction-tools-on

❌ Skipped https://safetycounselling.com/wp-content/uploads/2021/08/Construction-Site-Safety-Using-Extension-Ladders-Safely-by-Safety-Counselling-505-881-1112-scaled.jpg — 403 Client Error: Forbidden for url: https://safetycounselling.com/wp-content/uploads/2021/08/Construction-Site-Safety-Using-Extension-Ladders-Safely-by-Safety-Counselling-505-881-1112-scaled.jpg
❌ Skipped https://www.mrbricolage.com.cy/wp-content/uploads/2025/02/010-049-161-0301.jpg — 403 Client Error: Forbidden for url: https://www.mrbricolage.com.cy/wp-content/uploads/2025/02/010-049-161-0301.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/058/223/636/non_2x/a-glyph-style-icon-of-construction-ladder-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/058/223/636/non_2x/a-glyph-style-icon-of-construction-ladder-vector.jpg
❌ Skipped https://www.theladders.com/static/images/ladders-default-og.jpg — 403 Client Error: Forbidden for url: https://www.

ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/180818354/photo/male-construction-worker-climbing-ladder.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/488947244/photo/construction-ladder-in-wooden-building-restoration.jpg
ERROR:downloader:Response status code 400, file https://media.gettyimages.com/id/522998432/photo/construction-workers-renovating-building.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/1199844198/photo/wooden-ladders-and-unfinished-buildings-in-the-construction-site.jpg
ERROR:downloader:Response status code 403, file https://www.insideadvisorpro.com/wp-content/uploads/2023/09/Young-man-carrying-ladder-on-construction-site.jpg
ERROR:downloader:Response status code 404, file https://i0.wp.com/civilnoteppt.com/wp-content/uploads/2022/10/19-Types-of-Ladders-All-Guide-on-Ladder.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/157

...

❌ Skipped https://www.bigw.com.au/medias/sys_master/images/images/hf6/he9/102472694399006.jpg — HTTPSConnectionPool(host='www.bigw.com.au', port=443): Read timed out. (read timeout=10)
❌ Skipped https://www.bigw.com.au/medias/sys_master/images/images/h2d/h26/102472701149214.jpg — HTTPSConnectionPool(host='www.bigw.com.au', port=443): Read timed out. (read timeout=10)
❌ Skipped https://www.1800cpap.com/SC+Item+Images/resmed-mirage-liberty-full-face-cpap-mask.01.jpg — 404 Client Error: Not Found for url: https://1800cpap.com/SC+Item+Images/resmed-mirage-liberty-full-face-cpap-mask.01.jpg
❌ Skipped https://pubs.acs.org/cms/10.1021/acs.chas.1c00016/asset/images/large/hs1c00016_0003.jpeg — 403 Client Error: Forbidden for url: https://pubs.acs.org/cms/10.1021/acs.chas.1c00016/asset/images/large/hs1c00016_0003.jpeg
❌ Skipped https://www.planerium.com/wp-content/uploads/2023/02/face-mask-template-planerium.jpg — 403 Client Error: Forbidden for url: https://www.planerium.com/wp-content/uploads/

ERROR:downloader:Response status code 404, file https://www.stellaya.com/cdn/shop/files/fm_e3b66249-cbe1-4084-915c-98f0e34fc2f9_800x.jpg
ERROR:downloader:Response status code 403, file https://img2.cgtrader.com/items/3654923/cebb56988e/balaclava-mask-pack-marvelous-designer-3d-model-obj-zpac.jpg
ERROR:downloader:Response status code 403, file https://img1.cgtrader.com/items/3654923/e0f35dcc03/balaclava-mask-pack-marvelous-designer-3d-model-obj-zpac.jpg
ERROR:downloader:Exception caught when downloading file https://fishingproductspro.com/wp-content/uploads/sites/2064/2020/04/81180G18rUL._AC_SL1500_.jpg, error: HTTPSConnectionPool(host='fishingproductspro.com', port=443): Max retries exceeded with url: /wp-content/uploads/sites/2064/2020/04/81180G18rUL._AC_SL1500_.jpg (Caused by NameResolutionError("<urllib3.connection.HTTPSConnection object at 0x78ac60e84e60>: Failed to resolve 'fishingproductspro.com' ([Errno -2] Name or service not known)")), remaining retry times: 2
ERROR:downloader

❌ Skipped https://www.platousport.com/wp-content/uploads/2022/07/Lemae-Balaclava-Black-Front-View.jpg — 403 Client Error: Forbidden for url: https://www.platousport.com/wp-content/uploads/2022/07/Lemae-Balaclava-Black-Front-View.jpg
❌ Skipped https://c.stocksy.com/a/B7RE00/z9/3440825.jpg — 403 Client Error: Forbidden for url: https://c.stocksy.com/a/B7RE00/z9/3440825.jpg
❌ Skipped https://www.mddmask.com/uploads/202029524/anti-dust-earloop-face-mask54354872244.jpg — 403 Client Error: Forbidden for url: https://www.mddmask.com/uploads/202029524/anti-dust-earloop-face-mask54354872244.jpg
❌ Skipped https://cloud.jpnn.com/photo/jatim/news/normal/2024/01/26/kepala-instalasi-gawat-darurat-igd-rs-hasan-sadikin-bandung-tcso.jpg — 403 Client Error: Forbidden for url: https://cloud.jpnn.com/photo/jatim/news/normal/2024/01/26/kepala-instalasi-gawat-darurat-igd-rs-hasan-sadikin-bandung-tcso.jpg
❌ Skipped https://www.lexpressproperty.com/IMG/distant/jpg/bDu9cFIEJysNae48.jpg — 403 Client Error: Forb

ERROR:downloader:Response status code 410, file https://www.tigerfishtools.com/wp-content/uploads/2023/06/A-Guide-To-Respirators-Used-For-Dust-In-Construction.jpg
ERROR:downloader:Response status code 404, file https://cdn-bnbfb.nitrocdn.com/DqFztFvpsEAAoHJeycFBvLhiagHurYBp/assets/static/optimized/rev-6404aab/www.toolsreview.uk/wp-content/uploads/2020/11/f5a06f41cf02d78f3f42dbc78e7253cf.Best-Dust-Masks.jpg
ERROR:downloader:Response status code 403, file https://www.rebelsafetygear.com/wp-content/uploads/2020/02/RSG_NEW_MASK_FRONT-1024x1024.jpg
ERROR:downloader:Response status code 404, file https://i0.wp.com/howtohardscape.com/wp-content/uploads/2020/04/pure-guardian-disposable-respirators-fm3910-64_1000.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/1203919682/photo/builder-in-respirator-and-hardhat.jpg
ERROR:downloader:Response status code 400, file https://media.istockphoto.com/id/1214985844/photo/safety-respirator-dust-mask-set-on-a-cement-back

❌ Skipped https://www.tigerfishtools.com/wp-content/uploads/2023/06/A-Guide-To-Respirators-Used-For-Dust-In-Construction.jpg — 410 Client Error: Gone for url: https://www.tigerfishtools.com/wp-content/uploads/2023/06/A-Guide-To-Respirators-Used-For-Dust-In-Construction.jpg
❌ Skipped https://imgaz.staticbg.com/images/oaupload/ser1/banggood/images/84/B3/6f7cf1a8-d059-4534-aae7-51a7a175d586.jpg — 403 Client Error: Forbidden for url: https://imgaz.staticbg.com/images/oaupload/ser1/banggood/images/84/B3/6f7cf1a8-d059-4534-aae7-51a7a175d586.jpg
❌ Skipped https://static.vecteezy.com/system/resources/previews/054/665/462/non_2x/illustration-of-dust-mask-vector.jpg — 403 Client Error: Forbidden for url: https://static.vecteezy.com/system/resources/previews/054/665/462/non_2x/illustration-of-dust-mask-vector.jpg
❌ Skipped https://www.mddmask.com/uploads/202029524/anti-dust-earloop-face-mask54354872244.jpg — 403 Client Error: Forbidden for url: https://www.mddmask.com/uploads/202029524/anti-dust-

In [ ]:
!ls

boots  c_vest  gloves	helmet	msk	truck
crn    exvtr   goggles	ldr	s_cone	worker


Optional: Bellow you can see I used 800 image per class for labeling beacuse I have another plan for the images. You can use the the whole image for labling.

In [ ]:
import os

base_dir = "/content/for_label"

folders = [
    "boots", "c_vest", "gloves", "helmet", "msk", "truck",
    "crn", "exvtr", "goggles", "ldr", "s_cone", "worker"
]

results = {}

for folder in folders:
    folder_path = os.path.join(base_dir, folder)
    total_files = 0
    total_size = 0

    if os.path.exists(folder_path):
        for root, _, files in os.walk(folder_path):
            total_files += len(files)
            total_size += sum(os.path.getsize(os.path.join(root, f)) for f in files)

    results[folder] = {
        "files": total_files,
        "size_MB": round(total_size / (1024 * 1024), 2)  # convert to MB
    }

for folder, stats in results.items():
    print(f"{folder:8} -> {stats['files']:5} files, {stats['size_MB']:8.2f} MB")

# Grand total
total_files = sum(stats["files"] for stats in results.values())
total_size = sum(stats["size_MB"] for stats in results.values())
print("\nTOTAL    ->", total_files, "files,", round(total_size, 2), "MB")


boots    ->   800 files,   136.53 MB
c_vest   ->   800 files,   117.30 MB
gloves   ->   800 files,   137.16 MB
helmet   ->   800 files,    98.57 MB
msk      ->   800 files,   114.84 MB
truck    ->   800 files,   219.54 MB
crn      ->   800 files,   245.36 MB
exvtr    ->   800 files,   284.41 MB
goggles  ->   800 files,    89.41 MB
ldr      ->   800 files,   188.21 MB
s_cone   ->   800 files,   133.06 MB
worker   ->   800 files,   197.64 MB

TOTAL    -> 9600 files, 1962.03 MB


In [ ]:
!zip -r for_label.zip /content/for_label

Streaming output truncated to the last 5000 lines.
  adding: content/for_label/exvtr/exvtr_bing_excavator_000046.jpg (deflated 0%)
  adding: content/for_label/exvtr/exvtr_bing_construction_excavator_000239.jpg (deflated 1%)
  adding: content/for_label/exvtr/exvtr_google_heavy_duty_excavator_000050.jpg (deflated 0%)
  adding: content/for_label/exvtr/exvtr_bing_cat_excavator_000055.jpg (deflated 1%)
  adding: content/for_label/exvtr/exvtr_google_heavy_duty_excavator_000047.jpg (deflated 15%)
  adding: content/for_label/exvtr/exvtr_duck_heavy_duty_excavator_000023.jpg (deflated 9%)
  adding: content/for_label/exvtr/exvtr_google_cat_excavator_000061.jpg (deflated 1%)
  adding: content/for_label/exvtr/exvtr_bing_heavy_duty_excavator_000028.jpg (deflated 1%)
  adding: content/for_label/exvtr/exvtr_bing_construction_excavator_000293.jpg (deflated 21%)
  adding: content/for_label/exvtr/exvtr_bing_cat_excavator_000042.jpg (deflated 1%)
  adding: content/for_label/exvtr/exvtr_bing_excavator_0002

In [ ]:
!pip install kaggle -q


In [ ]:
!mkdir -p ~/.kaggle
!mv /content/kaggle.json ~/.kaggle/


In [ ]:
!chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!mkdir kaggle_up

In [ ]:
!kaggle datasets init -p /content/kaggle_up

Data package template written to: /content/kaggle_up/dataset-metadata.json


In [ ]:
!mv /content/for_label.zip /content/kaggle_up

In [ ]:
!kaggle datasets create -p /content/kaggle_up

Skipping folder: .ipynb_checkpoints; use '--dir-mode' to upload folders
Starting upload for file for_label.zip
100% 1.85G/1.85G [00:20<00:00, 96.2MB/s]
Upload successful: for_label.zip (2GB)
Your private Dataset is being created. Please check progress at https://www.kaggle.com/datasets/hasnatabdullah/fldhrhdie
